## Importing Packages {-}

In [1]:
import math
import os
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import spacy
import re
import contractions
import nltk
from nltk.tokenize import word_tokenize
from nltk import WordNetLemmatizer
import spacy
nlp = spacy.load('en_core_web_sm')
all_stopwords = nlp.Defaults.stop_words
lemmatizer = WordNetLemmatizer()
sp = spacy.load('en_core_web_sm')
all_stopwords = sp.Defaults.stop_words

from typing import List
import sys

sys.path.append('.')
import pandas as pd
import os

import string
from nltk.corpus import stopwords
from functools import reduce

In [2]:
import warnings
warnings.filterwarnings('ignore', category=DeprecationWarning)

import gensim
import gensim.corpora as corpora
import gensim.models

import os
from gensim.models.wrappers import LdaMallet
os.environ.update({'MALLET_HOME':r'/mallet-2.0.8'})
from gensim.models import CoherenceModel

!pip install pyLDAvis
import pyLDAvis
import pyLDAvis.gensim_models
pyLDAvis.enable_notebook()

import logging
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.ERROR)

from pprint import pprint

distutils: /Applications/anaconda3/include/python3.8/UNKNOWN
sysconfig: /Applications/anaconda3/include/python3.8
user = False
home = None
root = None
prefix = None
distutils: /Applications/anaconda3/include/python3.8/UNKNOWN
sysconfig: /Applications/anaconda3/include/python3.8
user = False
home = None
root = None
prefix = None


## Importing DataFrame {-}

In [3]:
dia_df = pd.read_csv('/Users/JoKerry/Desktop/CSML1030 - Machine Learning Capstone/mimic_clinical_outcome_prediction/ICD_Prediction/1. data_preparation/dia_df_prepared.csv')
dia_df

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


id                                               text  \
0      159643  CHIEF COMPLAINT: \n\nPRESENT ILLNESS: This 60 ...   
1      147171  CHIEF COMPLAINT: Substernal Chest Pain\n\nPRES...   
2      190531  CHIEF COMPLAINT: chest pain\n\nPRESENT ILLNESS...   
3      140536  CHIEF COMPLAINT: Presented with respiratory di...   
4      172808  CHIEF COMPLAINT: \n\nPRESENT ILLNESS: The pati...   
...       ...                                                ...   
11532  100746  CHIEF COMPLAINT: Hematemesis and fevers\n\nPRE...   
11533  137725  CHIEF COMPLAINT: Altered mental status, fever,...   
11534  159602  CHIEF COMPLAINT: Respiratory distress\n\nPRESE...   
11535  172011  CHIEF COMPLAINT: Chest pain and shortness of b...   
11536  171528  CHIEF COMPLAINT: Chest pain\n\nPRESENT ILLNESS...   

                                             short_codes  top_icd  
0                       424,428,276,997,427,414,412,V458      424  
1                                410,428,997,427,414,458      410  
2      414,428,584,486,411,585,276,250,403,440,V450,2...      414  
3      410,486,276,425,414,427,695,401,416,496,356,43...      410  
4                           410,998,997,427,414,362,V158      410  
...                                                  ...      ...  
11532  038,507,599,999,578,438,995,451,E879,707,496,4...       38  
11533  038,599,584,591,276,293,518,250,294,287,280,40...       38  
11534  038,518,486,584,427,008,496,424,995,519,V440,1...       38  
11535  414,349,518,285,438,997,427,250,412,461,V498,2...      414  
11536  414,281,411,401,272,427,V586,V103,365,715,564,...      414  

[11537 rows x 4 columns]

## Text Cleaning {-}

In [4]:
my_stop_words = ['discharge', 'diagnosis', 'medications', 'medication', 'disposition', 'condition', 'instructions', 
                 'status', 'secondary', 'changes', 'instruction', 'change', 'home', 'name', 'hospital', 'daily',
                'hour', 'follow', 'care', 'time', 'day', 'week', 'with', 'disp', 'discharged', 'admitted', 
                 'namepattern', 'none', 'chief', 'complaint', 'physical', 'exam', 'present', 'illness', 'family',
                 'year', 'history','admission', 'social', 'medical', 'allergies']

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [6]:
X = dia_df.text
X

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


0        CHIEF COMPLAINT: \n\nPRESENT ILLNESS: This 60 ...
1        CHIEF COMPLAINT: Substernal Chest Pain\n\nPRES...
2        CHIEF COMPLAINT: chest pain\n\nPRESENT ILLNESS...
3        CHIEF COMPLAINT: Presented with respiratory di...
4        CHIEF COMPLAINT: \n\nPRESENT ILLNESS: The pati...
                               ...                        
11532    CHIEF COMPLAINT: Hematemesis and fevers\n\nPRE...
11533    CHIEF COMPLAINT: Altered mental status, fever,...
11534    CHIEF COMPLAINT: Respiratory distress\n\nPRESE...
11535    CHIEF COMPLAINT: Chest pain and shortness of b...
11536    CHIEF COMPLAINT: Chest pain\n\nPRESENT ILLNESS...
Name: text, Length: 11537, dtype: object

In [7]:
documents = []

stemmer = WordNetLemmatizer()

for sen in range(0, len(X)):
    # Remove all the special characters
    document = re.sub(r'\W', ' ', str(X[sen]))
    # Remove new line characters
    document = document.replace("\n", ' ')
    # Punctuation
    document = re.sub(r'[^\w\s]', ' ', document)
    # remove all single characters
    document = re.sub(r'\s+[a-zA-Z]\s+', ' ', document)
    # Remove single characters from the start
    document = re.sub(r'\^[a-zA-Z]\s+', ' ', document) 
    # Substituting multiple spaces with single space
    document = re.sub(r'\s+', ' ', document, flags=re.I)
    # Removing prefixed 'b'
    document = re.sub(r'^b\s+', '', document)
    #Removing Numbers
    document = ''.join(i for i in document if not i.isdigit())
    #Removing Stopwords
    document = ' '.join([i for i in document.split() if not i in all_stopwords])
    #Removing certain sized words
    document = ' '.join([i for i in document.split() if len(i)>3])
    # Contractions
    document = contractions.fix(document)
    # Converting to Lowercase
    document = document.lower()
    # Lemmatization
    document = document.split()
    document = [stemmer.lemmatize(word) for word in document]
    document = ' '.join(document)
    #Removing my_stop_words
    document = ' '.join([i for i in document.split() if not i in my_stop_words])
    
    #return document
    documents.append(document)

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [8]:
X = documents
X

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


['this white male known murmur childhood post inferior myocardial infarction anteroseptal myocardial infarction post angioplasty since increased dyspnea exertion echocardiogram revealed aortic stenosis gradient ejection fraction apical akinesis cardiac catheterization revealed ejection fraction mitral regurgitation moderate left anterior descending lesion diagonal lesion right coronary artery occlusion aortic valve replacement coronary artery bypass graft significant skin cancer left shoulder hypothyroidism hypercholesterolemia hypertension coronary artery disease post angioplasty post inferior myocardial infarction anteroseptal myocardial infarction prozac synthroid pravachol toprol altace aspirin allergy known drug allergy significant coronary artery disease smoke cigar occasionally drink alcohol occasionally',
 'substernal chest pain male smoker presented experiencing sscp working excavating shoveling dirt state pain sharp crescendoed initially located right chest progressed involve

In [9]:
tokenized_words = [word_tokenize(i) for i in X]

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [10]:
tokenized_words

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


[['this',
  'white',
  'male',
  'known',
  'murmur',
  'childhood',
  'post',
  'inferior',
  'myocardial',
  'infarction',
  'anteroseptal',
  'myocardial',
  'infarction',
  'post',
  'angioplasty',
  'since',
  'increased',
  'dyspnea',
  'exertion',
  'echocardiogram',
  'revealed',
  'aortic',
  'stenosis',
  'gradient',
  'ejection',
  'fraction',
  'apical',
  'akinesis',
  'cardiac',
  'catheterization',
  'revealed',
  'ejection',
  'fraction',
  'mitral',
  'regurgitation',
  'moderate',
  'left',
  'anterior',
  'descending',
  'lesion',
  'diagonal',
  'lesion',
  'right',
  'coronary',
  'artery',
  'occlusion',
  'aortic',
  'valve',
  'replacement',
  'coronary',
  'artery',
  'bypass',
  'graft',
  'significant',
  'skin',
  'cancer',
  'left',
  'shoulder',
  'hypothyroidism',
  'hypercholesterolemia',
  'hypertension',
  'coronary',
  'artery',
  'disease',
  'post',
  'angioplasty',
  'post',
  'inferior',
  'myocardial',
  'infarction',
  'anteroseptal',
  'myocard

In [11]:
topic_modeling_series = pd.Series(tokenized_words)

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [12]:
topic_modeling_series

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


0        [this, white, male, known, murmur, childhood, ...
1        [substernal, chest, pain, male, smoker, presen...
2        [chest, pain, female, dmii, presented, transfe...
3        [presented, respiratory, distress, outside, tr...
4        [patient, male, previous, coronary, artery, di...
                               ...                        
11532    [hematemesis, fever, copd, residual, left, sid...
11533    [altered, mental, fever, hypotension, patient,...
11534    [respiratory, distress, female, tracheobronchi...
11535    [chest, pain, shortness, breath, this, male, k...
11536    [chest, pain, woman, hypertension, hyperlipide...
Length: 11537, dtype: object

## Topic Modelling {-}

In [13]:
# Create Dictionary
id2word = corpora.Dictionary(topic_modeling_series) #use entire corpus
id2word.filter_extremes(no_below=20, no_above=0.1)

# Create Corpus
texts = topic_modeling_series

# Term Document Frequency
corpus = [id2word.doc2bow(text) for text in texts]

# View
print(corpus)

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)
IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [14]:
print(id2word)

Dictionary(4484 unique tokens: ['akinesis', 'altace', 'angioplasty', 'anteroseptal', 'apical']...)


/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [15]:
def compute_coherence_values(dictionary, corpus, texts, limit, start=2, step=3):
    """
    Compute c_v coherence for various number of topics

    Parameters:
    ----------
    dictionary : Gensim dictionary
    corpus : Gensim corpus
    texts : List of input texts
    limit : Max num of topics

    Returns:
    -------
    model_list : List of LDA topic models
    coherence_values : Coherence values corresponding to the LDA model with respective number of topics
    """
    coherence_values = []
    model_list = []
    for num_topics in range(start, limit, step):
        print('Calculating {}-topic model'.format(num_topics))
        model = gensim.models.ldamodel.LdaModel(corpus=corpus, num_topics=num_topics, id2word=id2word)
        model_list.append(model)
        coherencemodel = CoherenceModel(model=model, texts=texts, dictionary=dictionary, coherence='c_v')
        coherence_values.append(coherencemodel.get_coherence())

    return model_list, coherence_values


/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [ ]:
# limit=20; start=2; step=1;
# model_list, coherence_values = compute_coherence_values(dictionary=id2word,
#                                                         corpus=corpus,
#                                                         texts=texts,
#                                                         start=start,
#                                                         limit=limit,
#                                                         step=step)

In [ ]:
# # show graph
# x = range(start, limit, step)
# plt.figure(figsize=(15, 10))
# plt.plot(x, coherence_values)
# plt.xlabel("Num Topics")
# plt.ylabel("Coherence score")
# plt.show()

In [17]:
# # Print the coherence scores
# for m, cv in zip(x, coherence_values):
#     print("Num Topics =", m, " has Coherence Value of", round(cv, 6))

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


## 20 Topics {-}

In [18]:
# Building LDA Model = LDA Model removing my_stop_words & featuring 30 topics
lda_model_optimal = gensim.models.ldamodel.LdaModel(corpus=corpus,
                                           id2word=id2word,
                                           num_topics=20, 
                                           random_state=100,
                                           update_every=1,
                                           chunksize=100,
                                           passes=10,
                                           alpha='auto',
                                           per_word_topics=True)

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [19]:
pprint(lda_model_optimal.print_topics(num_topics=20, num_words=15))
doc_lda = lda_model_optimal[corpus]

[(0,
  '0.215*"mitral" + 0.156*"regurgitation" + 0.115*"replacement" + '
  '0.047*"ventricular" + 0.045*"prolapse" + 0.039*"serial" + 0.021*"followed" '
  '+ 0.019*"congestive" + 0.018*"recreational" + 0.017*"aorta" + '
  '0.016*"grandfather" + 0.015*"lovastatin" + 0.014*"multivessel" + '
  '0.014*"root" + 0.014*"nsaid"'),
 (1,
  '0.061*"bilat" + 0.050*"occupation" + 0.043*"cigarette" + 0.039*"dental" + '
  '0.035*"reaction" + 0.033*"premature" + 0.032*"zocor" + 0.031*"adverse" + '
  '0.029*"caucasian" + 0.027*"incision" + 0.024*"clean" + 0.024*"asymptomatic" '
  '+ 0.023*"race" + 0.023*"telephone" + 0.021*"revascularization"'),
 (2,
  '0.078*"proximal" + 0.058*"circumflex" + 0.053*"main" + 0.048*"occlusion" + '
  '0.043*"occluded" + 0.038*"percent" + 0.035*"descending" + 0.034*"stenting" '
  '+ 0.021*"hypokinesis" + 0.021*"diffuse" + 0.020*"ostial" + 0.019*"branch" + '
  '0.018*"stented" + 0.017*"patent" + 0.017*"diagonal"'),
 (3,
  '0.017*"weakness" + 0.015*"diagnosed" + 0.013*"heada

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [20]:
# Compute Perplexity
print('\nPerplexity: ', lda_model_optimal.log_perplexity(corpus))  # a measure of how good the model is. lower the better.

# Compute Coherence Score
coherence_model_lda = CoherenceModel(model=lda_model_optimal, texts=texts, dictionary=id2word, coherence='c_v')
coherence_lda = coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_lda)

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)



Perplexity:  -10.617945615688155

Coherence Score:  0.5263091649141136


In [21]:
# Visualize the topics
pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim_models.prepare(lda_model_optimal, corpus, id2word)
vis

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)
/Applications/anaconda3/lib/python3.8/site-packages/pyLDAvis/_prepare.py:246: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  default_term_info = default_term_info.sort_values(


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
11     0.131202 -0.089829       1        1  15.943013
3      0.162809 -0.114535       2        1  10.912205
7      0.141314 -0.083350       3        1   7.911707
5      0.029268  0.033560       4        1   7.814541
8     -0.041571 -0.101340       5        1   7.690715
4      0.126677 -0.217161       6        1   7.079776
18     0.033636  0.032011       7        1   6.117967
17     0.082272  0.097994       8        1   5.574744
16     0.091549  0.096764       9        1   4.380515
10     0.061405 -0.059943      10        1   4.317982
19     0.047416  0.018469      11        1   3.665238
2      0.031162  0.250798      12        1   2.828947
1     -0.078003 -0.034169      13        1   2.737123
12    -0.019490  0.270145      14        1   2.549018
6     -0.008720 -0.112926      15        1   2.417233
9     -0.013579 -0.055346      16        1   2.339028
15    -0.351922 -0.076472      17        1   1.862441
13    -0.050054  0.059445      18        1   1.473183
0     -0.033074  0.154721      19        1   1.348545
14    -0.342295 -0.068834      20        1   1.036078, topic_info=            Term         Freq        Total Category  logprob  loglift
1164       mouth  5386.000000  5386.000000  Default  30.0000  30.0000
12        mitral  2505.000000  2505.000000  Default  29.0000  29.0000
233      capsule  2385.000000  2385.000000  Default  28.0000  28.0000
183        other  2645.000000  2645.000000  Default  27.0000  27.0000
10         graft  2317.000000  2317.000000  Default  26.0000  26.0000
...          ...          ...          ...      ...      ...      ...
3846  quetiapine     0.060494     1.174691  Topic20 -11.9034   1.6035
3247        qhrs     0.060495     1.174716  Topic20 -11.9034   1.6035
2728     bipolar     0.060495     1.174736  Topic20 -11.9034   1.6035
2715     ascites     0.060496     1.174773  Topic20 -11.9034   1.6035
2808      dosage     0.060495     1.174790  Topic20 -11.9034   1.6034

[932 rows x 6 columns], token_table=      Topic      Freq         Term
term                              
2346     13  0.987329         abdm
803       4  0.628378     abnormal
803      13  0.369907     abnormal
1412      3  0.997156  abnormality
2252     11  0.998869      abscess
...     ...       ...          ...
1313      4  0.995682        zetia
1050     13  0.998478        zocor
2363     14  0.992285     zolpidem
754       6  0.903325        zosyn
754      15  0.095515        zosyn

[1324 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[12, 4, 8, 6, 9, 5, 19, 18, 17, 11, 20, 3, 2, 13, 7, 10, 16, 14, 1, 15])

## Vectors For Probabilities - 20 Topics {-}

In [22]:
vector = lda_model_optimal[corpus]  # get topic probability distribution for a document
vector

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [23]:
def Extract(vector):
    return [item[0] for item in vector]

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [24]:
vector_prob = Extract(vector)
vector_prob

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


[[(0, 0.0758261),
  (1, 0.035513867),
  (2, 0.09323936),
  (3, 0.038145673),
  (4, 0.01594671),
  (5, 0.113979556),
  (6, 0.0538609),
  (7, 0.027136298),
  (8, 0.028813038),
  (9, 0.1078795),
  (10, 0.03863882),
  (11, 0.06835194),
  (12, 0.10382075),
  (14, 0.026952557),
  (16, 0.019093506),
  (17, 0.11496405),
  (18, 0.012816599),
  (19, 0.015216757)],
 [(1, 0.01803934),
  (2, 0.01615406),
  (3, 0.017363613),
  (5, 0.015513926),
  (7, 0.22786066),
  (8, 0.018801428),
  (10, 0.013506976),
  (11, 0.26218563),
  (16, 0.059637927),
  (17, 0.08676129),
  (18, 0.18693869),
  (19, 0.048626244)],
 [(2, 0.026252247),
  (3, 0.03191516),
  (4, 0.032926247),
  (5, 0.09567924),
  (6, 0.011796921),
  (7, 0.014569921),
  (8, 0.14265114),
  (9, 0.010267457),
  (10, 0.11503216),
  (11, 0.16049024),
  (17, 0.01560602),
  (18, 0.30590254),
  (19, 0.014871408)],
 [(1, 0.02031223),
  (2, 0.010859532),
  (3, 0.05735239),
  (4, 0.03795706),
  (5, 0.042616725),
  (6, 0.040979423),
  (7, 0.078232825),
  (8, 

## Aligning Index with Column Titles - 20 Topics {-}

In [27]:
vector_prob_df = pd.DataFrame(vector_prob, columns=[0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19])
vector_prob_df.head()

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


0                 1                 2                 3   \
0    (0, 0.0758261)  (1, 0.035513867)   (2, 0.09323936)  (3, 0.038145673)   
1   (1, 0.01803934)   (2, 0.01615406)  (3, 0.017363613)  (5, 0.015513926)   
2  (2, 0.026252247)   (3, 0.03191516)  (4, 0.032926247)   (5, 0.09567924)   
3   (1, 0.02031223)  (2, 0.010859532)   (3, 0.05735239)   (4, 0.03795706)   
4  (1, 0.016922446)   (2, 0.08984186)  (3, 0.028274652)  (4, 0.010554582)   

                 4                 5                  6                  7   \
0   (4, 0.01594671)  (5, 0.113979556)     (6, 0.0538609)   (7, 0.027136298)   
1   (7, 0.22786066)  (8, 0.018801428)  (10, 0.013506976)   (11, 0.26218563)   
2  (6, 0.011796921)  (7, 0.014569921)    (8, 0.14265114)   (9, 0.010267457)   
3  (5, 0.042616725)  (6, 0.040979423)   (7, 0.078232825)    (8, 0.11007802)   
4  (5, 0.046928003)   (7, 0.12220013)   (8, 0.016977094)  (10, 0.032420166)   

                  8                 9                  10                 11  \
0   (8, 0.028813038)    (9, 0.1078795)   (10, 0.03863882)   (11, 0.06835194)   
1  (16, 0.059637927)  (17, 0.08676129)   (18, 0.18693869)  (19, 0.048626244)   
2   (10, 0.11503216)  (11, 0.16049024)   (17, 0.01560602)   (18, 0.30590254)   
3   (9, 0.028450081)   (11, 0.3129194)  (12, 0.032175437)  (13, 0.023174327)   
4   (11, 0.07619785)  (12, 0.13997807)    (16, 0.2199771)   (17, 0.06729026)   

                  12                 13                 14                15  \
0   (12, 0.10382075)  (14, 0.026952557)  (16, 0.019093506)  (17, 0.11496405)   
1               None               None               None              None   
2  (19, 0.014871408)               None               None              None   
3   (16, 0.03958617)  (17, 0.038681388)  (18, 0.096130826)  (19, 0.01292453)   
4  (18, 0.028551277)  (19, 0.079902075)               None              None   

                  16                 17    18    19  
0  (18, 0.012816599)  (19, 0.015216757)  None  None  
1               None               None  None  None  
2               None               None  None  None  
3               None               None  None  None  
4               None               None  None  None

In [28]:
def clean_df(df):
    #Create empty dataframe copy
    df2 = pd.DataFrame(np.zeros(df.shape), columns = df.columns)
    nrows = df.shape[0]
    ncolumns = df.shape[1]
    #Populate empty dataframe
    for i in range(nrows):
        #Create key:value pair of each row
        rowdict = dict(zip([x[0] for x in df.iloc[i] if x != None], [x[1] for x in df.iloc[i] if x != None]))
        #Populate row based off of 
        for j in range(ncolumns):
            if j in rowdict.keys():
                df2.iloc[i][j] = rowdict[j]
            else:
                df2.iloc[i][j] = None
    return df2

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [29]:
vector_prob_df_align = clean_df(vector_prob_df)
vector_prob_df_align.head()

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


0         1         2         3         4         5         6   \
0  0.075826  0.035514  0.093239  0.038146  0.015947  0.113980  0.053861   
1       NaN  0.018039  0.016154  0.017364       NaN  0.015514       NaN   
2       NaN       NaN  0.026252  0.031915  0.032926  0.095679  0.011797   
3       NaN  0.020312  0.010860  0.057352  0.037957  0.042617  0.040979   
4       NaN  0.016922  0.089842  0.028275  0.010555  0.046928       NaN   

         7         8         9         10        11        12        13  \
0  0.027136  0.028813  0.107879  0.038639  0.068352  0.103821       NaN   
1  0.227861  0.018801       NaN  0.013507  0.262186       NaN       NaN   
2  0.014570  0.142651  0.010267  0.115032  0.160490       NaN       NaN   
3  0.078233  0.110078  0.028450       NaN  0.312919  0.032175  0.023174   
4  0.122200  0.016977       NaN  0.032420  0.076198  0.139978       NaN   

         14  15        16        17        18        19  
0  0.026953 NaN  0.019094  0.114964  0.012817  0.015217  
1       NaN NaN  0.059638  0.086761  0.186939  0.048626  
2       NaN NaN       NaN  0.015606  0.305903  0.014871  
3       NaN NaN  0.039586  0.038681  0.096131  0.012925  
4       NaN NaN  0.219977  0.067290  0.028551  0.079902

In [30]:
vector_prob_df_align.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 11537 entries, 0 to 11536
Data columns (total 20 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   0       3894 non-null   float64
 1   1       8413 non-null   float64
 2   2       7268 non-null   float64
 3   3       11536 non-null  float64
 4   4       10388 non-null  float64
 5   5       11530 non-null  float64
 6   6       4827 non-null   float64
 7   7       11526 non-null  float64
 8   8       11483 non-null  float64
 9   9       6699 non-null   float64
 10  10      11172 non-null  float64
 11  11      11537 non-null  float64
 12  12      6740 non-null   float64
 13  13      4996 non-null   float64
 14  14      2279 non-null   float64
 15  15      1501 non-null   float64
 16  16      10170 non-null  float64
 17  17      11265 non-null  float64
 18  18      9018 non-null   float64
 19  19      10345 non-null  float64
dtypes: float64(20)
memory usage: 1.8 MB


/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [31]:
vector_prob_df_align

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


0         1         2         3         4         5         6   \
0      0.075826  0.035514  0.093239  0.038146  0.015947  0.113980  0.053861   
1           NaN  0.018039  0.016154  0.017364       NaN  0.015514       NaN   
2           NaN       NaN  0.026252  0.031915  0.032926  0.095679  0.011797   
3           NaN  0.020312  0.010860  0.057352  0.037957  0.042617  0.040979   
4           NaN  0.016922  0.089842  0.028275  0.010555  0.046928       NaN   
...         ...       ...       ...       ...       ...       ...       ...   
11532       NaN       NaN       NaN  0.191299  0.163605  0.017019  0.014533   
11533       NaN  0.017545       NaN  0.274455  0.113821  0.067834  0.058860   
11534  0.030176       NaN  0.019393  0.056023  0.262005  0.048550       NaN   
11535       NaN  0.095169  0.013687  0.048528  0.017124  0.116095       NaN   
11536       NaN  0.073882  0.024519  0.061730       NaN  0.076067       NaN   

             7         8         9         10        11        12        13  \
0      0.027136  0.028813  0.107879  0.038639  0.068352  0.103821       NaN   
1      0.227861  0.018801       NaN  0.013507  0.262186       NaN       NaN   
2      0.014570  0.142651  0.010267  0.115032  0.160490       NaN       NaN   
3      0.078233  0.110078  0.028450       NaN  0.312919  0.032175  0.023174   
4      0.122200  0.016977       NaN  0.032420  0.076198  0.139978       NaN   
...         ...       ...       ...       ...       ...       ...       ...   
11532  0.142502  0.156996  0.024599  0.017947  0.179022       NaN  0.029364   
11533  0.085894  0.077710  0.034336  0.013975  0.159301       NaN       NaN   
11534  0.213907  0.101222       NaN  0.010962  0.186225       NaN       NaN   
11535  0.043671  0.080010       NaN  0.062560  0.126418       NaN       NaN   
11536  0.017736  0.183787       NaN  0.049139  0.102746       NaN       NaN   

             14        15        16        17        18        19  
0      0.026953       NaN  0.019094  0.114964  0.012817  0.015217  
1           NaN       NaN  0.059638  0.086761  0.186939  0.048626  
2           NaN       NaN       NaN  0.015606  0.305903  0.014871  
3           NaN       NaN  0.039586  0.038681  0.096131  0.012925  
4           NaN       NaN  0.219977  0.067290  0.028551  0.079902  
...         ...       ...       ...       ...       ...       ...  
11532       NaN       NaN       NaN  0.010755  0.016680       NaN  
11533       NaN  0.018699       NaN  0.020903  0.016936  0.016336  
11534       NaN       NaN  0.011365  0.013608       NaN       NaN  
11535       NaN  0.042054  0.014946  0.220287  0.069744  0.012835  
11536       NaN  0.207478  0.013408  0.143401       NaN       NaN  

[11537 rows x 20 columns]

In [32]:
topics = vector_prob_df_align
labels = dia_df['top_icd']

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [33]:
topic_modeling_results_20 = pd.concat([labels, topics], axis=1)
topic_modeling_results_20

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


top_icd         0         1         2         3         4         5  \
0          424  0.075826  0.035514  0.093239  0.038146  0.015947  0.113980   
1          410       NaN  0.018039  0.016154  0.017364       NaN  0.015514   
2          414       NaN       NaN  0.026252  0.031915  0.032926  0.095679   
3          410       NaN  0.020312  0.010860  0.057352  0.037957  0.042617   
4          410       NaN  0.016922  0.089842  0.028275  0.010555  0.046928   
...        ...       ...       ...       ...       ...       ...       ...   
11532       38       NaN       NaN       NaN  0.191299  0.163605  0.017019   
11533       38       NaN  0.017545       NaN  0.274455  0.113821  0.067834   
11534       38  0.030176       NaN  0.019393  0.056023  0.262005  0.048550   
11535      414       NaN  0.095169  0.013687  0.048528  0.017124  0.116095   
11536      414       NaN  0.073882  0.024519  0.061730       NaN  0.076067   

              6         7         8  ...        10        11        12  \
0      0.053861  0.027136  0.028813  ...  0.038639  0.068352  0.103821   
1           NaN  0.227861  0.018801  ...  0.013507  0.262186       NaN   
2      0.011797  0.014570  0.142651  ...  0.115032  0.160490       NaN   
3      0.040979  0.078233  0.110078  ...       NaN  0.312919  0.032175   
4           NaN  0.122200  0.016977  ...  0.032420  0.076198  0.139978   
...         ...       ...       ...  ...       ...       ...       ...   
11532  0.014533  0.142502  0.156996  ...  0.017947  0.179022       NaN   
11533  0.058860  0.085894  0.077710  ...  0.013975  0.159301       NaN   
11534       NaN  0.213907  0.101222  ...  0.010962  0.186225       NaN   
11535       NaN  0.043671  0.080010  ...  0.062560  0.126418       NaN   
11536       NaN  0.017736  0.183787  ...  0.049139  0.102746       NaN   

             13        14        15        16        17        18        19  
0           NaN  0.026953       NaN  0.019094  0.114964  0.012817  0.015217  
1           NaN       NaN       NaN  0.059638  0.086761  0.186939  0.048626  
2           NaN       NaN       NaN       NaN  0.015606  0.305903  0.014871  
3      0.023174       NaN       NaN  0.039586  0.038681  0.096131  0.012925  
4           NaN       NaN       NaN  0.219977  0.067290  0.028551  0.079902  
...         ...       ...       ...       ...       ...       ...       ...  
11532  0.029364       NaN       NaN       NaN  0.010755  0.016680       NaN  
11533       NaN       NaN  0.018699       NaN  0.020903  0.016936  0.016336  
11534       NaN       NaN       NaN  0.011365  0.013608       NaN       NaN  
11535       NaN       NaN  0.042054  0.014946  0.220287  0.069744  0.012835  
11536       NaN       NaN  0.207478  0.013408  0.143401       NaN       NaN  

[11537 rows x 21 columns]

In [34]:
topic_modeling_results_20.isna().sum()

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


top_icd        0
0           7643
1           3124
2           4269
3              1
4           1149
5              7
6           6710
7             11
8             54
9           4838
10           365
11             0
12          4797
13          6541
14          9258
15         10036
16          1367
17           272
18          2519
19          1192
dtype: int64

In [35]:
topic_modeling_results_20 = topic_modeling_results_20.fillna(0)
topic_modeling_results_20

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


top_icd         0         1         2         3         4         5  \
0          424  0.075826  0.035514  0.093239  0.038146  0.015947  0.113980   
1          410  0.000000  0.018039  0.016154  0.017364  0.000000  0.015514   
2          414  0.000000  0.000000  0.026252  0.031915  0.032926  0.095679   
3          410  0.000000  0.020312  0.010860  0.057352  0.037957  0.042617   
4          410  0.000000  0.016922  0.089842  0.028275  0.010555  0.046928   
...        ...       ...       ...       ...       ...       ...       ...   
11532       38  0.000000  0.000000  0.000000  0.191299  0.163605  0.017019   
11533       38  0.000000  0.017545  0.000000  0.274455  0.113821  0.067834   
11534       38  0.030176  0.000000  0.019393  0.056023  0.262005  0.048550   
11535      414  0.000000  0.095169  0.013687  0.048528  0.017124  0.116095   
11536      414  0.000000  0.073882  0.024519  0.061730  0.000000  0.076067   

              6         7         8  ...        10        11        12  \
0      0.053861  0.027136  0.028813  ...  0.038639  0.068352  0.103821   
1      0.000000  0.227861  0.018801  ...  0.013507  0.262186  0.000000   
2      0.011797  0.014570  0.142651  ...  0.115032  0.160490  0.000000   
3      0.040979  0.078233  0.110078  ...  0.000000  0.312919  0.032175   
4      0.000000  0.122200  0.016977  ...  0.032420  0.076198  0.139978   
...         ...       ...       ...  ...       ...       ...       ...   
11532  0.014533  0.142502  0.156996  ...  0.017947  0.179022  0.000000   
11533  0.058860  0.085894  0.077710  ...  0.013975  0.159301  0.000000   
11534  0.000000  0.213907  0.101222  ...  0.010962  0.186225  0.000000   
11535  0.000000  0.043671  0.080010  ...  0.062560  0.126418  0.000000   
11536  0.000000  0.017736  0.183787  ...  0.049139  0.102746  0.000000   

             13        14        15        16        17        18        19  
0      0.000000  0.026953  0.000000  0.019094  0.114964  0.012817  0.015217  
1      0.000000  0.000000  0.000000  0.059638  0.086761  0.186939  0.048626  
2      0.000000  0.000000  0.000000  0.000000  0.015606  0.305903  0.014871  
3      0.023174  0.000000  0.000000  0.039586  0.038681  0.096131  0.012925  
4      0.000000  0.000000  0.000000  0.219977  0.067290  0.028551  0.079902  
...         ...       ...       ...       ...       ...       ...       ...  
11532  0.029364  0.000000  0.000000  0.000000  0.010755  0.016680  0.000000  
11533  0.000000  0.000000  0.018699  0.000000  0.020903  0.016936  0.016336  
11534  0.000000  0.000000  0.000000  0.011365  0.013608  0.000000  0.000000  
11535  0.000000  0.000000  0.042054  0.014946  0.220287  0.069744  0.012835  
11536  0.000000  0.000000  0.207478  0.013408  0.143401  0.000000  0.000000  

[11537 rows x 21 columns]

In [36]:
topic_modeling_results_20.isna().sum()

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


top_icd    0
0          0
1          0
2          0
3          0
4          0
5          0
6          0
7          0
8          0
9          0
10         0
11         0
12         0
13         0
14         0
15         0
16         0
17         0
18         0
19         0
dtype: int64

## CSV {-}

In [38]:
topic_modeling_results_20.to_csv('topic_model_dia_20_topics.csv', index=False)

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


## Topic Modeling - 50 Topics {-}

In [39]:
# Building LDA Model = LDA Model removing my_stop_words & featuring 30 topics
lda_model_optimal = gensim.models.ldamodel.LdaModel(corpus=corpus,
                                           id2word=id2word,
                                           num_topics=50, 
                                           random_state=100,
                                           update_every=1,
                                           chunksize=100,
                                           passes=10,
                                           alpha='auto',
                                           per_word_topics=True)

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [40]:
pprint(lda_model_optimal.print_topics(num_topics=50, num_words=15))
doc_lda = lda_model_optimal[corpus]

[(0,
  '0.110*"ischemic" + 0.088*"stage" + 0.085*"dialysis" + 0.067*"fistula" + '
  '0.066*"accident" + 0.061*"attack" + 0.047*"hemodialysis" + '
  '0.046*"cerebrovascular" + 0.044*"consult" + 0.041*"transient" + '
  '0.040*"said" + 0.029*"group" + 0.025*"tachypnea" + 0.024*"tear" + '
  '0.024*"procrit"'),
 (1,
  '0.072*"drop" + 0.060*"fall" + 0.053*"fracture" + 0.046*"osteoarthritis" + '
  '0.038*"wine" + 0.037*"glass" + 0.037*"osteoporosis" + 0.027*"partial" + '
  '0.026*"widowed" + 0.025*"glaucoma" + 0.025*"level" + 0.025*"hearing" + '
  '0.023*"elderly" + 0.022*"diverticulosis" + 0.021*"weekly"'),
 (2,
  '0.095*"wound" + 0.061*"picc" + 0.049*"bacteremia" + 0.048*"former" + '
  '0.040*"failed" + 0.037*"attempted" + 0.036*"process" + 0.032*"summary" + '
  '0.030*"macular" + 0.030*"rule" + 0.029*"staff" + 0.029*"linezolid" + '
  '0.029*"read" + 0.029*"receiving" + 0.027*"grandchild"'),
 (3,
  '0.187*"stenting" + 0.179*"vascular" + 0.120*"aneurysm" + 0.093*"diagonal" + '
  '0.080*"osti

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [41]:
# Compute Perplexity
print('\nPerplexity: ', lda_model_optimal.log_perplexity(corpus))  # a measure of how good the model is. lower the better.

# Compute Coherence Score
coherence_model_lda = CoherenceModel(model=lda_model_optimal, texts=texts, dictionary=id2word, coherence='c_v')
coherence_lda = coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_lda)

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)



Perplexity:  -14.8939550876417

Coherence Score:  0.4364674859908806


In [42]:
# Visualize the topics
pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim_models.prepare(lda_model_optimal, corpus, id2word)
vis

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)
/Applications/anaconda3/lib/python3.8/site-packages/pyLDAvis/_prepare.py:246: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  default_term_info = default_term_info.sort_values(


PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
48    -0.129584 -0.004644       1        1  7.141586
5     -0.101823  0.023288       2        1  6.807555
49    -0.021239 -0.083311       3        1  6.447889
34    -0.009881 -0.044718       4        1  5.958116
43     0.052995  0.110115       5        1  3.864792
27    -0.301525  0.202795       6        1  3.341025
7     -0.015780 -0.047687       7        1  3.275193
30     0.014751 -0.015306       8        1  3.071309
29    -0.014064 -0.054082       9        1  2.970529
11    -0.032103 -0.031458      10        1  2.872378
15    -0.026313 -0.030990      11        1  2.770732
16    -0.029086 -0.061056      12        1  2.679077
17    -0.110843  0.024652      13        1  2.661066
1      0.008465 -0.009026      14        1  2.186240
10     0.013567 -0.029076      15        1  2.130589
4     -0.043853 -0.019071      16        1  2.089698
33     0.206615  0.303793      17        1  1.935911
22     0.025175 -0.026675      18        1  1.887922
41     0.024909 -0.030364      19        1  1.850103
18     0.027943 -0.027472      20        1  1.808647
39     0.010644 -0.022479      21        1  1.704749
32    -0.323116  0.168951      22        1  1.648189
21     0.000118 -0.030032      23        1  1.597738
8      0.027821 -0.041783      24        1  1.576100
12     0.176796  0.328677      25        1  1.500943
9     -0.003483 -0.005478      26        1  1.437783
24     0.020531 -0.035418      27        1  1.422622
26    -0.004345 -0.013956      28        1  1.324190
40     0.021711 -0.024631      29        1  1.294258
20     0.024975 -0.040549      30        1  1.225666
37     0.046396  0.097246      31        1  1.166085
45    -0.044119 -0.035319      32        1  1.113648
42     0.029035 -0.033712      33        1  1.061868
13     0.030204 -0.026315      34        1  1.029210
19     0.031856 -0.026843      35        1  1.017545
31    -0.001156 -0.009199      36        1  1.008317
2      0.023294 -0.025344      37        1  0.998239
25     0.040138 -0.023967      38        1  0.976877
0      0.028923 -0.025226      39        1  0.940174
14     0.042377 -0.011212      40        1  0.918790
6      0.018533 -0.050830      41        1  0.889999
38     0.026612 -0.026838      42        1  0.884584
44     0.029705 -0.045974      43        1  0.848854
47     0.033834 -0.029263      44        1  0.786670
3      0.035634 -0.034898      45        1  0.776390
35     0.034553 -0.027898      46        1  0.743525
36     0.018939  0.001598      47        1  0.729082
23     0.010460 -0.039218      48        1  0.643865
28     0.038019 -0.030321      49        1  0.497229
46     0.036784 -0.029475      50        1  0.486453, topic_info=               Term         Freq        Total Category  logprob  loglift
1164          mouth  4895.000000  4895.000000  Default  30.0000  30.0000
10            graft  2237.000000  2237.000000  Default  29.0000  29.0000
12           mitral  2076.000000  2076.000000  Default  28.0000  28.0000
33    approximately  1748.000000  1748.000000  Default  27.0000  27.0000
183           other  2503.000000  2503.000000  Default  26.0000  26.0000
...             ...          ...          ...      ...      ...      ...
4            apical     0.022837   590.844267  Topic50 -12.1215  -4.8351
5         childhood     0.022837   116.018410  Topic50 -12.1215  -3.2073
6             cigar     0.022837   289.954544  Topic50 -12.1215  -4.1233
7        descending     0.022837  1555.032544  Topic50 -12.1215  -5.8028
8          diagonal     0.022837   776.162891  Topic50 -12.1215  -5.1079

[1852 rows x 6 columns], token_table=      Topic      Freq        Term
term                             
802      31  0.983667       _____
223      22  0.995560  abdominial
2134     24  0.996601    ablation
360       1  0.176109        able
360       3  0.141372        able
...     ...       ...         ...
1179     36  0.

## Creating Vectors For Probabilities - 50 Topics {-}

In [43]:
vector = lda_model_optimal[corpus]  # get topic probability distribution for a document
vector

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [44]:
def Extract(vector):
    return [item[0] for item in vector]

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [45]:
vector_prob = Extract(vector)
vector_prob

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


[[(1, 0.013534429),
  (3, 0.016913267),
  (4, 0.010527915),
  (5, 0.07059643),
  (6, 0.024927815),
  (7, 0.017937187),
  (8, 0.010431606),
  (10, 0.030576536),
  (11, 0.017548414),
  (15, 0.07993411),
  (16, 0.046714567),
  (17, 0.015488044),
  (18, 0.011352445),
  (19, 0.021871803),
  (22, 0.011964668),
  (23, 0.034869935),
  (25, 0.021279536),
  (27, 0.013531232),
  (28, 0.113404624),
  (29, 0.019207552),
  (30, 0.013518388),
  (34, 0.038642593),
  (35, 0.020987723),
  (40, 0.023662705),
  (41, 0.011434973),
  (43, 0.03692967),
  (45, 0.052162744),
  (48, 0.036415342),
  (49, 0.027814245)],
 [(1, 0.014247814),
  (3, 0.010265662),
  (5, 0.057881128),
  (7, 0.06017059),
  (8, 0.02801745),
  (10, 0.022057317),
  (11, 0.040043946),
  (16, 0.04715785),
  (17, 0.22977911),
  (18, 0.028474418),
  (21, 0.019498866),
  (27, 0.037488565),
  (29, 0.01853378),
  (32, 0.031868063),
  (34, 0.050611977),
  (36, 0.010887668),
  (41, 0.019440278),
  (43, 0.057378035),
  (47, 0.010465963),
  (48, 0.06

## Align Index With Column Titles - 50 Topics {-}

In [50]:
vector_prob_df = pd.DataFrame(vector_prob, columns=[0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,
                                                    31,32,33,34,35,36,37,38])
vector_prob_df.head()

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


0                 1                 2                 3   \
0  (1, 0.013534429)  (3, 0.016913267)  (4, 0.010527915)   (5, 0.07059643)   
1  (1, 0.014247814)  (3, 0.010265662)  (5, 0.057881128)   (7, 0.06017059)   
2  (0, 0.056808632)  (1, 0.012584273)   (5, 0.03472139)  (7, 0.015886841)   
3   (1, 0.04779465)   (2, 0.01443357)  (4, 0.034415152)  (5, 0.053815957)   
4  (1, 0.010063181)  (2, 0.016066397)    (5, 0.0687971)  (7, 0.059853237)   

                  4                  5                   6   \
0   (6, 0.024927815)   (7, 0.017937187)    (8, 0.010431606)   
1    (8, 0.02801745)  (10, 0.022057317)   (11, 0.040043946)   
2   (8, 0.010104555)  (10, 0.025561556)   (11, 0.015378413)   
3    (6, 0.01378229)    (7, 0.07883611)     (8, 0.05258371)   
4  (10, 0.045415822)   (11, 0.01465273)  (15, 0.0144697195)   

                  7                  8                  9   ...    29    30  \
0  (10, 0.030576536)  (11, 0.017548414)   (15, 0.07993411)  ...  None  None   
1   (16, 0.04715785)   (17, 0.22977911)  (18, 0.028474418)  ...  None  None   
2  (14, 0.020501986)   (16, 0.03620287)  (17, 0.043630205)  ...  None  None   
3    (9, 0.05839199)  (10, 0.029616894)   (11, 0.12639351)  ...  None  None   
4   (16, 0.11617676)  (17, 0.023395084)  (27, 0.010794231)  ...  None  None   

     31    32    33    34    35    36    37    38  
0  None  None  None  None  None  None  None  None  
1  None  None  None  None  None  None  None  None  
2  None  None  None  None  None  None  None  None  
3  None  None  None  None  None  None  None  None  
4  None  None  None  None  None  None  None  None  

[5 rows x 39 columns]

In [51]:
def clean_df(df):
    #Create empty dataframe copy
    df2 = pd.DataFrame(np.zeros(df.shape), columns = df.columns)
    nrows = df.shape[0]
    ncolumns = df.shape[1]
    #Populate empty dataframe
    for i in range(nrows):
        #Create key:value pair of each row
        rowdict = dict(zip([x[0] for x in df.iloc[i] if x != None], [x[1] for x in df.iloc[i] if x != None]))
        #Populate row based off of 
        for j in range(ncolumns):
            if j in rowdict.keys():
                df2.iloc[i][j] = rowdict[j]
            else:
                df2.iloc[i][j] = None
    return df2

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [52]:
vector_prob_df_align = clean_df(vector_prob_df)
vector_prob_df_align.head()

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


0         1         2         3         4         5         6   \
0       NaN  0.013534       NaN  0.016913  0.010528  0.070596  0.024928   
1       NaN  0.014248       NaN  0.010266       NaN  0.057881       NaN   
2  0.056809  0.012584       NaN       NaN       NaN  0.034721       NaN   
3       NaN  0.047795  0.014434       NaN  0.034415  0.053816  0.013782   
4       NaN  0.010063  0.016066       NaN       NaN  0.068797       NaN   

         7         8         9   ...        29        30  31        32  \
0  0.017937  0.010432       NaN  ...  0.019208  0.013518 NaN       NaN   
1  0.060171  0.028017       NaN  ...  0.018534       NaN NaN  0.031868   
2  0.015887  0.010105       NaN  ...       NaN  0.029535 NaN       NaN   
3  0.078836  0.052584  0.058392  ...  0.019986  0.012825 NaN  0.058279   
4  0.059853       NaN       NaN  ...  0.151158  0.010051 NaN       NaN   

         33        34        35        36        37        38  
0       NaN  0.038643  0.020988       NaN       NaN       NaN  
1       NaN  0.050612       NaN  0.010888       NaN       NaN  
2  0.036078  0.023628       NaN       NaN  0.015739       NaN  
3       NaN  0.016454       NaN       NaN       NaN  0.014221  
4       NaN  0.148035       NaN       NaN       NaN       NaN  

[5 rows x 39 columns]

In [53]:
vector_prob_df_align.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 11537 entries, 0 to 11536
Data columns (total 39 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   0       2812 non-null   float64
 1   1       9746 non-null   float64
 2   2       2978 non-null   float64
 3   3       2847 non-null   float64
 4   4       7526 non-null   float64
 5   5       11537 non-null  float64
 6   6       2160 non-null   float64
 7   7       11154 non-null  float64
 8   8       7559 non-null   float64
 9   9       4957 non-null   float64
 10  10      9726 non-null   float64
 11  11      11135 non-null  float64
 12  12      1045 non-null   float64
 13  13      3082 non-null   float64
 14  14      3023 non-null   float64
 15  15      10738 non-null  float64
 16  16      9785 non-null   float64
 17  17      10463 non-null  float64
 18  18      8605 non-null   float64
 19  19      3106 non-null   float64
 20  20      4041 non-null   float64
 21  21      6268 non-null   float64
 22

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [54]:
vector_prob_df_align

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


0         1         2         3         4         5         6   \
0           NaN  0.013534       NaN  0.016913  0.010528  0.070596  0.024928   
1           NaN  0.014248       NaN  0.010266       NaN  0.057881       NaN   
2      0.056809  0.012584       NaN       NaN       NaN  0.034721       NaN   
3           NaN  0.047795  0.014434       NaN  0.034415  0.053816  0.013782   
4           NaN  0.010063  0.016066       NaN       NaN  0.068797       NaN   
...         ...       ...       ...       ...       ...       ...       ...   
11532  0.018651       NaN       NaN       NaN  0.013709  0.041725       NaN   
11533       NaN       NaN       NaN  0.017797  0.013119  0.080651       NaN   
11534       NaN       NaN       NaN       NaN  0.123818  0.031651       NaN   
11535       NaN  0.012027       NaN  0.018741       NaN  0.141891       NaN   
11536       NaN  0.092522       NaN       NaN       NaN  0.060959       NaN   

             7         8         9   ...        29        30        31  \
0      0.017937  0.010432       NaN  ...  0.019208  0.013518       NaN   
1      0.060171  0.028017       NaN  ...  0.018534       NaN       NaN   
2      0.015887  0.010105       NaN  ...       NaN  0.029535       NaN   
3      0.078836  0.052584  0.058392  ...  0.019986  0.012825       NaN   
4      0.059853       NaN       NaN  ...  0.151158  0.010051       NaN   
...         ...       ...       ...  ...       ...       ...       ...   
11532  0.017319       NaN  0.020428  ...  0.010365  0.061598  0.011793   
11533  0.015280  0.020225  0.060907  ...  0.016880  0.116687       NaN   
11534  0.075292       NaN  0.058639  ...  0.013110  0.025966  0.025690   
11535  0.029863  0.023191       NaN  ...  0.017068  0.012012       NaN   
11536  0.010714       NaN  0.022763  ...  0.030201  0.018330  0.013676   

             32        33        34        35        36        37        38  
0           NaN       NaN  0.038643  0.020988       NaN       NaN       NaN  
1      0.031868       NaN  0.050612       NaN  0.010888       NaN       NaN  
2           NaN  0.036078  0.023628       NaN       NaN  0.015739       NaN  
3      0.058279       NaN  0.016454       NaN       NaN       NaN  0.014221  
4           NaN       NaN  0.148035       NaN       NaN       NaN       NaN  
...         ...       ...       ...       ...       ...       ...       ...  
11532       NaN  0.040981  0.080692       NaN       NaN       NaN       NaN  
11533       NaN       NaN  0.091467       NaN       NaN  0.016072  0.010190  
11534       NaN  0.016989  0.064101       NaN       NaN       NaN       NaN  
11535       NaN       NaN  0.050882       NaN  0.019682  0.034140       NaN  
11536       NaN  0.028251  0.041779       NaN  0.034635       NaN       NaN  

[11537 rows x 39 columns]

In [55]:
topics = vector_prob_df_align
labels = dia_df['top_icd']

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [56]:
topic_modeling_results_50 = pd.concat([labels, topics], axis=1)
topic_modeling_results_50

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


top_icd         0         1         2         3         4         5  \
0          424       NaN  0.013534       NaN  0.016913  0.010528  0.070596   
1          410       NaN  0.014248       NaN  0.010266       NaN  0.057881   
2          414  0.056809  0.012584       NaN       NaN       NaN  0.034721   
3          410       NaN  0.047795  0.014434       NaN  0.034415  0.053816   
4          410       NaN  0.010063  0.016066       NaN       NaN  0.068797   
...        ...       ...       ...       ...       ...       ...       ...   
11532       38  0.018651       NaN       NaN       NaN  0.013709  0.041725   
11533       38       NaN       NaN       NaN  0.017797  0.013119  0.080651   
11534       38       NaN       NaN       NaN       NaN  0.123818  0.031651   
11535      414       NaN  0.012027       NaN  0.018741       NaN  0.141891   
11536      414       NaN  0.092522       NaN       NaN       NaN  0.060959   

              6         7         8  ...        29        30        31  \
0      0.024928  0.017937  0.010432  ...  0.019208  0.013518       NaN   
1           NaN  0.060171  0.028017  ...  0.018534       NaN       NaN   
2           NaN  0.015887  0.010105  ...       NaN  0.029535       NaN   
3      0.013782  0.078836  0.052584  ...  0.019986  0.012825       NaN   
4           NaN  0.059853       NaN  ...  0.151158  0.010051       NaN   
...         ...       ...       ...  ...       ...       ...       ...   
11532       NaN  0.017319       NaN  ...  0.010365  0.061598  0.011793   
11533       NaN  0.015280  0.020225  ...  0.016880  0.116687       NaN   
11534       NaN  0.075292       NaN  ...  0.013110  0.025966  0.025690   
11535       NaN  0.029863  0.023191  ...  0.017068  0.012012       NaN   
11536       NaN  0.010714       NaN  ...  0.030201  0.018330  0.013676   

             32        33        34        35        36        37        38  
0           NaN       NaN  0.038643  0.020988       NaN       NaN       NaN  
1      0.031868       NaN  0.050612       NaN  0.010888       NaN       NaN  
2           NaN  0.036078  0.023628       NaN       NaN  0.015739       NaN  
3      0.058279       NaN  0.016454       NaN       NaN       NaN  0.014221  
4           NaN       NaN  0.148035       NaN       NaN       NaN       NaN  
...         ...       ...       ...       ...       ...       ...       ...  
11532       NaN  0.040981  0.080692       NaN       NaN       NaN       NaN  
11533       NaN       NaN  0.091467       NaN       NaN  0.016072  0.010190  
11534       NaN  0.016989  0.064101       NaN       NaN       NaN       NaN  
11535       NaN       NaN  0.050882       NaN  0.019682  0.034140       NaN  
11536       NaN  0.028251  0.041779       NaN  0.034635       NaN       NaN  

[11537 rows x 40 columns]

In [57]:
topic_modeling_results_50.isna().sum()

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


top_icd        0
0           8725
1           1791
2           8559
3           8690
4           4011
5              0
6           9377
7            383
8           3978
9           6580
10          1811
11           402
12         10492
13          8455
14          8514
15           799
16          1752
17          1074
18          2932
19          8431
20          7496
21          5269
22          2540
23          9791
24          7079
25          8734
26          6048
27          2150
28          9763
29           535
30          1772
31          7435
32          9670
33          6203
34             0
35          8824
36          8983
37          7787
38          8875
dtype: int64

In [58]:
topic_modeling_results_50 = topic_modeling_results_50.fillna(0)
topic_modeling_results_50

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


top_icd         0         1         2         3         4         5  \
0          424  0.000000  0.013534  0.000000  0.016913  0.010528  0.070596   
1          410  0.000000  0.014248  0.000000  0.010266  0.000000  0.057881   
2          414  0.056809  0.012584  0.000000  0.000000  0.000000  0.034721   
3          410  0.000000  0.047795  0.014434  0.000000  0.034415  0.053816   
4          410  0.000000  0.010063  0.016066  0.000000  0.000000  0.068797   
...        ...       ...       ...       ...       ...       ...       ...   
11532       38  0.018651  0.000000  0.000000  0.000000  0.013709  0.041725   
11533       38  0.000000  0.000000  0.000000  0.017797  0.013119  0.080651   
11534       38  0.000000  0.000000  0.000000  0.000000  0.123818  0.031651   
11535      414  0.000000  0.012027  0.000000  0.018741  0.000000  0.141891   
11536      414  0.000000  0.092522  0.000000  0.000000  0.000000  0.060959   

              6         7         8  ...        29        30        31  \
0      0.024928  0.017937  0.010432  ...  0.019208  0.013518  0.000000   
1      0.000000  0.060171  0.028017  ...  0.018534  0.000000  0.000000   
2      0.000000  0.015887  0.010105  ...  0.000000  0.029535  0.000000   
3      0.013782  0.078836  0.052584  ...  0.019986  0.012825  0.000000   
4      0.000000  0.059853  0.000000  ...  0.151158  0.010051  0.000000   
...         ...       ...       ...  ...       ...       ...       ...   
11532  0.000000  0.017319  0.000000  ...  0.010365  0.061598  0.011793   
11533  0.000000  0.015280  0.020225  ...  0.016880  0.116687  0.000000   
11534  0.000000  0.075292  0.000000  ...  0.013110  0.025966  0.025690   
11535  0.000000  0.029863  0.023191  ...  0.017068  0.012012  0.000000   
11536  0.000000  0.010714  0.000000  ...  0.030201  0.018330  0.013676   

             32        33        34        35        36        37        38  
0      0.000000  0.000000  0.038643  0.020988  0.000000  0.000000  0.000000  
1      0.031868  0.000000  0.050612  0.000000  0.010888  0.000000  0.000000  
2      0.000000  0.036078  0.023628  0.000000  0.000000  0.015739  0.000000  
3      0.058279  0.000000  0.016454  0.000000  0.000000  0.000000  0.014221  
4      0.000000  0.000000  0.148035  0.000000  0.000000  0.000000  0.000000  
...         ...       ...       ...       ...       ...       ...       ...  
11532  0.000000  0.040981  0.080692  0.000000  0.000000  0.000000  0.000000  
11533  0.000000  0.000000  0.091467  0.000000  0.000000  0.016072  0.010190  
11534  0.000000  0.016989  0.064101  0.000000  0.000000  0.000000  0.000000  
11535  0.000000  0.000000  0.050882  0.000000  0.019682  0.034140  0.000000  
11536  0.000000  0.028251  0.041779  0.000000  0.034635  0.000000  0.000000  

[11537 rows x 40 columns]

In [59]:
topic_modeling_results_50.isna().sum()

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


top_icd    0
0          0
1          0
2          0
3          0
4          0
5          0
6          0
7          0
8          0
9          0
10         0
11         0
12         0
13         0
14         0
15         0
16         0
17         0
18         0
19         0
20         0
21         0
22         0
23         0
24         0
25         0
26         0
27         0
28         0
29         0
30         0
31         0
32         0
33         0
34         0
35         0
36         0
37         0
38         0
dtype: int64

## CSV {-}

In [60]:
topic_modeling_results_50.to_csv('topic_model_dia_50_topics.csv', index=False)

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)
